In [2]:
!pip3 install --user tweepy==3.10.0
!pip install --upgrade google-cloud-pubsub

  Using cached tweepy-3.10.0-py2.py3-none-any.whl (30 kB)


In [1]:
#Import the necessary methods from tweepy library
import tweepy
from tweepy.streaming import StreamListener
from tweepy import OAuthHandler
from tweepy import Stream
import datetime
import json
import time
import sys

from google.cloud import pubsub_v1

In [2]:
#Variables that contains the user credentials to access Twitter API

# Twitter Application Management
# https://apps.twitter.com/

CONSUMER_KEY = "****"
CONSUMER_SECRET = "****"
ACCESS_TOKEN = "****"
ACCESS_TOKEN_SECRET = "****"

In [3]:
from google.cloud import pubsub_v1

In [4]:
# config to pubsub
publisher = pubsub_v1.PublisherClient()
topic_path = publisher.topic_path("ns01-project", "twitter")
print(topic_path)

projects/ns01-project/topics/twitter


In [5]:
"projects/ns01-project/topics/twitter" == topic_path

True

In [6]:
# Authenticate to twitter api config
auth = OAuthHandler(CONSUMER_KEY, CONSUMER_SECRET)
auth.set_access_token(ACCESS_TOKEN, ACCESS_TOKEN_SECRET)

In [7]:
# Tag
keyword = ["protest"]

In [8]:
def write_to_pubsub(data):
    try:
        publisher.publish(topic_path, data=json.dumps({
            "text": data["text"],
            "lang": data["lang"],
            "location": data["location"],
            "id": data["id"],
            "posted_at": datetime.datetime.fromtimestamp(data["created_at"]).strftime('%Y-%m-%d %H:%M:%S')
        }).encode("utf-8"), tweet_id=str(data["id"]).encode("utf-8"))
    except Exception as e:
        raise

In [9]:
def reformat_tweet(tweet):
    x = tweet

    processed_doc = {
        "id": x["id"],
        "location": x['user']['location'],
        "lang": x["lang"],
        "retweeted_id": x["retweeted_status"]["id"] if "retweeted_status" in x else None,
        "favorite_count": x["favorite_count"] if "favorite_count" in x else 0,
        "retweet_count": x["retweet_count"] if "retweet_count" in x else 0,
        "coordinates_latitude": x["coordinates"]["coordinates"][0] if x["coordinates"] else 0,
        "coordinates_longitude": x["coordinates"]["coordinates"][0] if x["coordinates"] else 0,
        "place": x["place"]["country_code"] if x["place"] else None,
        "user_id": x["user"]["id"],
        "created_at": time.mktime(time.strptime(x["created_at"], "%a %b %d %H:%M:%S +0000 %Y"))
    }

    if x["entities"]["hashtags"]:
        processed_doc["hashtags"] = [{"text": y["text"], "startindex": y["indices"][0]} for y in
                                     x["entities"]["hashtags"]]
    else:
        processed_doc["hashtags"] = []

    if x["entities"]["user_mentions"]:
        processed_doc["usermentions"] = [{"screen_name": y["screen_name"], "startindex": y["indices"][0]} for y in
                                         x["entities"]["user_mentions"]]
    else:
        processed_doc["usermentions"] = []

    if "extended_tweet" in x:
        processed_doc["text"] = x["extended_tweet"]["full_text"]
    elif "full_text" in x:
        processed_doc["text"] = x["full_text"]
    else:
        processed_doc["text"] = x["text"]

    return processed_doc

In [10]:
class StdOutListener(StreamListener):
    """ A listener handles tweets that are received from the stream.
    This is a basic listener that just pushes tweets to pubsub
    """

    def __init__(self):
        super(StdOutListener, self).__init__()
        self._counter = 0

    def on_status(self, data):
        write_to_pubsub(reformat_tweet(data._json))
        print(reformat_tweet(data._json))
        self._counter += 1
        return True

    def on_error(self, status):
        if status == 420:
            print("rate limit active")
            return False

In [ ]:
l = StdOutListener()
stream = tweepy.Stream(auth, l, tweet_mode='extended')
stream.filter(track=keyword)

{'id': 1468665145928867844, 'location': 'the simulation', 'lang': 'en', 'retweeted_id': 1468574977809129475, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 21196360, 'created_at': 1638992031.0, 'hashtags': [], 'usermentions': [{'screen_name': 'NadiaWhittomeMP', 'startindex': 3}], 'text': "RT @NadiaWhittomeMP: The Downing Street party revelations come as the government is pushing through Bills that will take away people's righ…"}
{'id': 1468665159304368128, 'location': None, 'lang': 'en', 'retweeted_id': 1468648194703831048, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 1451977136475029505, 'created_at': 1638992035.0, 'hashtags': [], 'usermentions': [{'screen_name': 'MintPressNews', 'startindex': 3}, {'screen_name': 'BTHeadline', 'startindex': 52}, {'screen_name': 'dancohen3000', 'startindex': 78}], 'text': 'RT @MintPressNews: "Media bear

{'id': 1468665226598010884, 'location': 'North London', 'lang': 'en', 'retweeted_id': None, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 2230643848, 'created_at': 1638992051.0, 'hashtags': [], 'usermentions': [], 'text': '🤣🤣 I say London does a massive street party and we get some glow sticks'}
{'id': 1468665229517410304, 'location': 'no maps for these territories', 'lang': 'en', 'retweeted_id': 1466002224404905986, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 889257473613451264, 'created_at': 1638992051.0, 'hashtags': [], 'usermentions': [{'screen_name': 'AnarchistFed', 'startindex': 3}], 'text': 'RT @AnarchistFed: Holy shit. \nThe extra 18 Pages of the Bill they added just fundamentally enshrine it as legislation to criminalise all fo…'}
{'id': 1468665231769583620, 'location': 'Mayo, Ireland', 'lang': 'en', 'retweeted_id': 146866310

{'id': 1468665282298273796, 'location': None, 'lang': 'und', 'retweeted_id': 1468661788682108939, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 961617644729372677, 'created_at': 1638992064.0, 'hashtags': [{'text': 'covid19nl', 'startindex': 18}, {'text': 'coronamaatregelen', 'startindex': 29}, {'text': 'coronapas', 'startindex': 48}, {'text': 'vaccinatieplicht', 'startindex': 59}, {'text': 'verzet', 'startindex': 77}, {'text': 'oostenrijk', 'startindex': 85}], 'usermentions': [{'screen_name': 'Simone_Voice', 'startindex': 3}], 'text': 'RT @Simone_Voice: #covid19nl #coronamaatregelen #coronapas #vaccinatieplicht #verzet #oostenrijk'}
{'id': 1468665286375133189, 'location': 'Scotland', 'lang': 'en', 'retweeted_id': 1468644209724952588, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 1391444646140817417, 'created_at': 1638992065.0, 'hashtags

{'id': 1468665355983892493, 'location': None, 'lang': 'und', 'retweeted_id': 1468610093532913673, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 1008115730389356544, 'created_at': 1638992082.0, 'hashtags': [], 'usermentions': [{'screen_name': 'egoldmanrevolt', 'startindex': 3}], 'text': 'RT @egoldmanrevolt: https://t.co/TsuBEUyMkL'}
{'id': 1468665359578415106, 'location': 'Texas, USA', 'lang': 'en', 'retweeted_id': 1468648194703831048, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 1171828482843824131, 'created_at': 1638992082.0, 'hashtags': [], 'usermentions': [{'screen_name': 'MintPressNews', 'startindex': 3}, {'screen_name': 'BTHeadline', 'startindex': 52}, {'screen_name': 'dancohen3000', 'startindex': 78}], 'text': 'RT @MintPressNews: "Media bears a responsibility" - @BTHeadline correspondent @dancohen3000 examines mainstream coverage

{'id': 1468665431628161027, 'location': 'Durban, South Africa', 'lang': 'en', 'retweeted_id': 1468519084820205576, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 1039043061156855809, 'created_at': 1638992100.0, 'hashtags': [], 'usermentions': [{'screen_name': 'ShakesRampedi', 'startindex': 3}], 'text': "RT @ShakesRampedi: - Chiefs not honoring the City fixture\n- Becker's resignation announced\n- Murphy resigns\n- Chiefs say they won't travel…"}
{'id': 1468665432567549952, 'location': 'Toronto, Ontario', 'lang': 'en', 'retweeted_id': None, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 2384049668, 'created_at': 1638992100.0, 'hashtags': [], 'usermentions': [], 'text': 'Chinese women protest in Guangdong province in 1921 demanding suffrage. https://t.co/6AR2n2B4Ia'}
{'id': 1468665450301206529, 'location': None, 'lang': 'en', 'retweeted_id'

...

{'id': 1468690660479827971, 'location': 'Earth', 'lang': 'en', 'retweeted_id': None, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 1355771558099210244, 'created_at': 1638998115.0, 'hashtags': [], 'usermentions': [{'screen_name': 'Francesco0996', 'startindex': 0}, {'screen_name': 'HangLoose1337', 'startindex': 15}, {'screen_name': 'Eng32Eric', 'startindex': 30}], 'text': '@Francesco0996 @HangLoose1337 @Eng32Eric Well actually in Japan you can get a gun you just have to take a course and pass with above 95%. And how are the freedoms there? If protest you get locked up. People are at the  play of government. Like how they have hereditary classes of people. Works good?'}
{'id': 1468690664015777792, 'location': None, 'lang': 'de', 'retweeted_id': 1468474775127441415, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 1180540710493327360, 'created

{'id': 1468690694118068226, 'location': None, 'lang': 'en', 'retweeted_id': 1468682001272250374, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 1164397654622629894, 'created_at': 1638998123.0, 'hashtags': [{'text': 'Munich', 'startindex': 42}], 'usermentions': [{'screen_name': 'disclosetv', 'startindex': 3}], 'text': 'RT @disclosetv: NOW - Germany: Protest in #Munich against compulsory vaccination.\n\nhttps://t.co/wy4TNYHKo8'}
{'id': 1468690696026603522, 'location': 'South East England ', 'lang': 'en', 'retweeted_id': 1468688294515032070, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 46114432, 'created_at': 1638998123.0, 'hashtags': [], 'usermentions': [{'screen_name': 'Valkyrie20201', 'startindex': 3}], 'text': 'RT @Valkyrie20201: Tonight is just the start of the protests. \n\nLondon chaos: Police and protesters fight hours after Boris 

{'id': 1468690731992862724, 'location': 'Ede', 'lang': 'und', 'retweeted_id': None, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 313409740, 'created_at': 1638998132.0, 'hashtags': [], 'usermentions': [], 'text': '😍😍😍😍😍😍😍👍🏻👍🏻👍🏻👍🏻👍🏻👍🏻'}
{'id': 1468690736178728966, 'location': 'East Hibernia', 'lang': 'en', 'retweeted_id': None, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 2701438088, 'created_at': 1638998133.0, 'hashtags': [], 'usermentions': [], 'text': "Families protest construction of mobile classrooms on Chicago's south side, 1963. https://t.co/MBTBvMAKGS"}
{'id': 1468690737877377029, 'location': 'CPH DK', 'lang': 'en', 'retweeted_id': 1468682001272250374, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 58175844, 'created_at': 1638998133.0, 'hashtags': [{'text

{'id': 1468690776867672081, 'location': 'London, England', 'lang': 'en', 'retweeted_id': 1468667717381242889, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 463823129, 'created_at': 1638998142.0, 'hashtags': [], 'usermentions': [{'screen_name': 'NewsForAllUK', 'startindex': 3}], 'text': 'RT @NewsForAllUK: 🚨 | NEW: Scuffles break out at a Kill the Bill protest outside Parliament.\n\n https://t.co/5exHm6EYiR'}
{'id': 1468690777316413440, 'location': None, 'lang': 'en', 'retweeted_id': 1468670378587439108, 'favorite_count': 0, 'retweet_count': 0, 'coordinates_latitude': 0, 'coordinates_longitude': 0, 'place': None, 'user_id': 2999478886, 'created_at': 1638998142.0, 'hashtags': [], 'usermentions': [{'screen_name': 'Samfr', 'startindex': 3}], 'text': 'RT @Samfr: Tory MPs declaring their opposition to attacks on liberty re: masks/vaccines while voting through a Borders Bill that allows the…'}
{'id': 146869077789528473

KeyboardInterrupt: 